In [1]:
pip install numpy keras tensorflow

Note: you may need to restart the kernel to use updated packages.


In [2]:
import numpy as np
import requests
import re
import keras
from tensorflow.keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.utils import to_categorical
from keras.models import Sequential
from keras.layers import Embedding, LSTM, Dense, Dropout
import string

2024-05-21 21:10:52.467840: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [3]:
url = "https://storage.googleapis.com/download.tensorflow.org/data/shakespeare.txt"  
try:
    # Send a GET request to the URL to fetch the data
    response = requests.get(url)
        
    # Check if the request was successful (status code 200)
    if response.status_code == 200:
        # Extract the text content from the response
        text_data = response.text
        print(text_data)
    else:
        print("Failed to retrieve data from the provided link. Status code:", response.status_code)
except Exception as e:
    print("An error occurred:", e)

First Citizen:
Before we proceed any further, hear me speak.

All:
Speak, speak.

First Citizen:
You are all resolved rather to die than to famish?

All:
Resolved. resolved.

First Citizen:
First, you know Caius Marcius is chief enemy to the people.

All:
We know't, we know't.

First Citizen:
Let us kill him, and we'll have corn at our own price.
Is't a verdict?

All:
No more talking on't; let it be done: away, away!

Second Citizen:
One word, good citizens.

First Citizen:
We are accounted poor citizens, the patricians good.
What authority surfeits on would relieve us: if they
would yield us but the superfluity, while it were
wholesome, we might guess they relieved us humanely;
but they think we are too dear: the leanness that
afflicts us, the object of our misery, is as an
inventory to particularise their abundance; our
sufferance is a gain to them Let us revenge this with
our pikes, ere we become rakes: for the gods know I
speak this in hunger for bread, not in thirst for revenge.



In [4]:
split1 = text_data.split()
paragraph = ' '.join(split1)
lowercased_text = paragraph.lower()
print(lowercased_text)

first citizen: before we proceed any further, hear me speak. all: speak, speak. first citizen: you are all resolved rather to die than to famish? all: resolved. resolved. first citizen: first, you know caius marcius is chief enemy to the people. all: we know't, we know't. first citizen: let us kill him, and we'll have corn at our own price. is't a verdict? all: no more talking on't; let it be done: away, away! second citizen: one word, good citizens. first citizen: we are accounted poor citizens, the patricians good. what authority surfeits on would relieve us: if they would yield us but the superfluity, while it were wholesome, we might guess they relieved us humanely; but they think we are too dear: the leanness that afflicts us, the object of our misery, is as an inventory to particularise their abundance; our sufferance is a gain to them let us revenge this with our pikes, ere we become rakes: for the gods know i speak this in hunger for bread, not in thirst for revenge. second cit

In [6]:
sentences = re.split(r'(?<=[.?!]) +', lowercased_text)
    
no_names = []
    
# Iterate through each sentence
for sentence in sentences:
    # Split the sentence at the first colon
    part = sentence.split(":", 1)
        
    # Check if there's a colon in the sentence
    if len(part) > 1:
        # Get the text after the colon, stripped of leading/trailing whitespace
        after_colon = part[1].strip()
        no_names.append(after_colon)
    
#print(no_names)

no_names_3 = ' '.join(no_names)

In [7]:
no_char = no_names_3.translate(str.maketrans('', '', string.punctuation))
print(no_char)

before we proceed any further hear me speak speak speak you are all resolved rather to die than to famish resolved first you know caius marcius is chief enemy to the people we knowt we knowt let us kill him and well have corn at our own price no more talking ont let it be done away away one word good citizens we are accounted poor citizens the patricians good if they would yield us but the superfluity while it were wholesome we might guess they relieved us humanely but they think we are too dear the leanness that afflicts us the object of our misery is as an inventory to particularise their abundance our sufferance is a gain to them let us revenge this with our pikes ere we become rakes for the gods know i speak this in hunger for bread not in thirst for revenge would you proceed especially against caius marcius against him first hes a very dog to the commonalty consider you what services he has done for his country very well and could be content to give him good report fort but that h

In [8]:
# Tokenize text using .split() function
tokens = no_char.split()
print(tokens)
total_words = len(tokens) + 1

['before', 'we', 'proceed', 'any', 'further', 'hear', 'me', 'speak', 'speak', 'speak', 'you', 'are', 'all', 'resolved', 'rather', 'to', 'die', 'than', 'to', 'famish', 'resolved', 'first', 'you', 'know', 'caius', 'marcius', 'is', 'chief', 'enemy', 'to', 'the', 'people', 'we', 'knowt', 'we', 'knowt', 'let', 'us', 'kill', 'him', 'and', 'well', 'have', 'corn', 'at', 'our', 'own', 'price', 'no', 'more', 'talking', 'ont', 'let', 'it', 'be', 'done', 'away', 'away', 'one', 'word', 'good', 'citizens', 'we', 'are', 'accounted', 'poor', 'citizens', 'the', 'patricians', 'good', 'if', 'they', 'would', 'yield', 'us', 'but', 'the', 'superfluity', 'while', 'it', 'were', 'wholesome', 'we', 'might', 'guess', 'they', 'relieved', 'us', 'humanely', 'but', 'they', 'think', 'we', 'are', 'too', 'dear', 'the', 'leanness', 'that', 'afflicts', 'us', 'the', 'object', 'of', 'our', 'misery', 'is', 'as', 'an', 'inventory', 'to', 'particularise', 'their', 'abundance', 'our', 'sufferance', 'is', 'a', 'gain', 'to', 'th

In [9]:
# Create a dictionary to map tokens to unique integers
token_to_id = {token: idx for idx, token in enumerate(set(tokens))}
# Encode the tokens using the dictionary
encoded_tokens = [token_to_id[token] for token in tokens]
#print(token_to_id)
print(encoded_tokens)

[5326, 8452, 9609, 541, 6674, 1163, 7312, 4728, 4728, 4728, 4628, 9403, 6085, 6234, 9214, 3882, 7958, 3640, 3882, 3211, 6234, 7431, 4628, 6383, 9437, 9238, 573, 5081, 5707, 3882, 8033, 724, 8452, 956, 8452, 956, 7717, 1886, 5136, 3623, 2140, 6420, 5874, 1903, 7679, 7726, 6449, 2569, 4495, 5243, 3282, 5598, 7717, 5924, 2367, 2877, 6097, 6097, 1776, 2591, 781, 2096, 8452, 9403, 7732, 2162, 2096, 8033, 2327, 781, 6471, 8493, 2433, 3611, 1886, 9800, 8033, 6917, 5725, 5924, 8405, 787, 8452, 8922, 2768, 8493, 104, 1886, 3578, 9800, 8493, 4333, 8452, 9403, 3908, 5301, 8033, 2350, 3143, 9177, 1886, 8033, 1833, 3168, 7726, 1391, 573, 608, 1036, 1213, 3882, 2468, 1131, 4819, 7726, 7040, 573, 3425, 7057, 3882, 9305, 7717, 1886, 2876, 9469, 1000, 7726, 2826, 9327, 8452, 156, 9831, 2682, 8033, 4376, 6383, 2797, 4728, 9469, 6533, 7890, 2682, 3465, 1901, 6533, 6932, 2682, 2876, 2433, 4628, 9609, 7500, 6777, 9437, 9238, 6777, 3623, 7431, 2978, 3425, 9062, 3931, 3882, 8033, 1896, 7479, 4628, 4083, 3644

In [10]:
# Create sequences of 5 words for X and 1 word for y
input_sequences = []
sequence_length = 5

for i in range(sequence_length, len(encoded_tokens)):
    n_gram_sequence = encoded_tokens[i-sequence_length:i+1]
    input_sequences.append(n_gram_sequence)

# Convert to numpy array
input_sequences = np.array(input_sequences)

# Create predictors and labels
X = input_sequences[:,:-1]
y = input_sequences[:,-1]
print(X)

# Convert labels to categorical
y = to_categorical(y, num_classes=total_words)

[[5326 8452 9609  541 6674]
 [8452 9609  541 6674 1163]
 [9609  541 6674 1163 7312]
 ...
 [3072 5358 9214 3649 7597]
 [5358 9214 3649 7597 4753]
 [9214 3649 7597 4753 3178]]
